# imports

In [ ]:
# mount drive
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!pip install -q transformers torch spacy spacytextblob tqdm

     |████████████████████████████████| 4.4 MB 7.5 MB/s 
     |████████████████████████████████| 101 kB 13.3 MB/s 
     |████████████████████████████████| 6.6 MB 43.5 MB/s 
     |████████████████████████████████| 596 kB 65.1 MB/s 


In [ ]:
import pandas as pd
import numpy as np
import transformers
import torch
import torch.nn.functional as F
import spacy
from tqdm.notebook import tqdm
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()

# pull the data

- analyst_ratings = pd.read_csv(analyst_fp)
- raw_partner_headlines = pd.read_csv(raw_partner_headlines_fp)

In [ ]:
analyst_fp = 'drive/MyDrive/Datathon/Data/sentiment-stocks/analyst_ratings_processed.csv'
raw_partner_headlines_fp = 'drive/MyDrive/Datathon/Data/sentiment-stocks/raw_partner_headlines.csv'
sentiment_analyst_fp = 'drive/MyDrive/Datathon/Data/sentiment-stocks/analyst_ratings_processed_sentiment.csv'
sentiment_analyst_ratings_2013_19_fp = 'drive/MyDrive/Datathon/Data/sentiment-stocks/analyst_ratings_processed_sentiment_2013_19.csv'
sentiment_raw_partner_headlines_2013_19_fp = 'drive/MyDrive/Datathon/Data/sentiment-stocks/sentiment_raw_partner_headlines_2013_19.csv'
sentiment_raw_partner_headlines_fp = 'drive/MyDrive/Datathon/Data/sentiment-stocks/raw_partner_headlines_sentiment.csv'

In [ ]:
# analyst_ratings = pd.read_csv(analyst_fp)
# raw_partner_headlines = pd.read_csv(raw_partner_headlines_fp)
# sentiment_analyst_ratings = pd.read_csv(sentiment_analyst_fp)
# sentiment_raw_partner_headlines = pd.read_csv(sentiment_raw_partner_headlines_fp)
sentiment_analyst_ratings_2013_19 = pd.read_csv(sentiment_analyst_ratings_2013_19_fp)
sentiment_raw_partner_headlines_2013_19 = pd.read_csv(sentiment_raw_partner_headlines_2013_19_fp)

In [ ]:
def add_month_year(*dfs):
  for df in dfs:
    df['month_year'] = df.date.apply(lambda x: str(x)[:7])
add_month_year(sentiment_analyst_ratings_2013_19, sentiment_raw_partner_headlines_2013_19)

In [ ]:
sentiment_analyst_ratings.groupby('year').count()

In [ ]:
sentiment_raw_partner_headlines.groupby('month_year').count()
sentiment_raw_partner_headlines['year'] = sentiment_raw_partner_headlines.month_year.apply(lambda x: int(x[:4]))
sentiment_raw_partner_headlines.groupby('year').count()

# Load a model

## Load a pretrained model from spacy

In [ ]:
from spacytextblob.spacytextblob import SpacyTextBlob
nlp = spacy.load('en_core_web_sm')
nlp.add_pipe('spacytextblob')

titles = raw_partner_headlines.headline.tolist()
sentiments = [doc._.blob.polarity for doc in tqdm(nlp.pipe(titles), total=len(titles))]

In [ ]:
raw_partner_headlines['spacy_sentiment'] = sentiments
raw_partner_headlines.to_csv('drive/MyDrive/Datathon/Data/sentiment-stocks/raw_partner_headlines_sentiment.csv', index=False)

# Load a pretrained model from huggingface transformers

- ahmedrachid/FinancialBERT-Sentiment-Analysis

In [ ]:
%%capture
from transformers import AutoTokenizer, AutoModelForSequenceClassification

tokenizer = AutoTokenizer.from_pretrained("mrm8488/distilroberta-finetuned-financial-news-sentiment-analysis")

model = AutoModelForSequenceClassification.from_pretrained("mrm8488/distilroberta-finetuned-financial-news-sentiment-analysis")
device = 'cuda' if torch.cuda.is_available() else 'cpu'
model.to(device)

In [ ]:
# sentiment_raw_partner_headlines_2013_19_sample = sentiment_raw_partner_headlines_2013_19.groupby('month_year').sample(5)
# sentiment_analyst_ratings_2013_19_sample = sentiment_analyst_ratings_2013_19.groupby('month_year').sample(5)

In [ ]:
# headline_titles = sentiment_raw_partner_headlines.headline.str.lower()
# analyst_titles = sentiment_analyst_ratings.title.str.lower()

headline_titles = sentiment_raw_partner_headlines_2013_19.headline.str.lower()
analyst_titles = sentiment_analyst_ratings_2013_19.title.str.lower()

# max_analyst_length = analyst_ratings.title.str.len().max()
# max_headline_length = headline_titles.str.len().max()
# max_token_length = -1
# for title in headline_titles:
#   if len(title) == max_headline_length:
#     max_token_length = max(max_token_length, len(tokenizer.tokenize(title)))
# max_token_length

In [ ]:
from torch.utils.data import Dataset, DataLoader

class ReviewDataset(Dataset):

  def __init__(self, reviews, tokenizer, max_len):
    self.reviews = reviews
    self.tokenizer = tokenizer
    self.max_len = max_len
  
  def __len__(self):
    return len(self.reviews)
  
  def __getitem__(self, item):
    review = str(self.reviews.iloc[item])
    encoding = self.tokenizer.encode_plus(
      review,
      add_special_tokens=True,
      max_length=self.max_len,
      return_token_type_ids=False,
      padding='max_length',
      return_attention_mask=True,
      return_tensors='pt',
    )

    return {
      'input_ids': encoding['input_ids'].flatten(),
      'attention_mask': encoding['attention_mask'].flatten(),
    }

def make_dataloader(df, tokenizer, max_len, batch_size):
  dataset = ReviewDataset(df, tokenizer, max_len)
  return DataLoader(dataset, batch_size=batch_size, num_workers=4, pin_memory=True)
batch_size = 64
analyst_titles_dataloader = make_dataloader(df=analyst_titles, tokenizer=tokenizer, max_len=135, batch_size=batch_size)
partner_headlines_dataloader = make_dataloader(df=headline_titles, tokenizer=tokenizer, max_len=135, batch_size=batch_size)

In [ ]:
model_logits = []

model.to(device)
model.eval()
with torch.no_grad():
  for batch in tqdm(partner_headlines_dataloader):
    input_ids, attention_mask = batch['input_ids'], batch['attention_mask']
    input_ids = input_ids.to(device)
    attention_mask = attention_mask.to(device)
    output = model(input_ids=input_ids, attention_mask=attention_mask)
    model_logits.append(output.logits)

In [ ]:
# deal with model_logits[-1] separately
big_logits = torch.stack(model_logits[:-1])
softmax_logits = F.softmax(big_logits, dim=2)
values, indices = softmax_logits.max(dim=2)
scores = (indices - 1) * values
scores_list = scores.reshape(64 * len(model_logits[:-1])).tolist()
print(len(scores_list), type(scores_list))

softmax_logits = F.softmax(model_logits[-1])
values, indices = softmax_logits.max(dim=1)
scores = (indices - 1) * values
scores_list.extend(scores.reshape(softmax_logits.shape[0]).tolist())
print(scores_list[-10:])

In [ ]:
sentiment_analyst_ratings_2013_19.to_csv(sentiment_analyst_ratings_2013_19_fp, index=False)

In [ ]:
sns.set_style("white")

SMALL_SIZE = 10
MEDIUM_SIZE = 30
BIGGER_SIZE = 40

plt.rc('font', size=SMALL_SIZE)          # controls default text sizes
plt.rc('axes', titlesize=SMALL_SIZE)     # fontsize of the axes title
plt.rc('axes', labelsize=MEDIUM_SIZE)    # fontsize of the x and y labels
plt.rc('xtick', labelsize=MEDIUM_SIZE)    # fontsize of the tick labels
plt.rc('ytick', labelsize=MEDIUM_SIZE)    # fontsize of the tick labels
plt.rc('legend', fontsize=SMALL_SIZE)    # legend fontsize
plt.rc('figure', titlesize=BIGGER_SIZE)  # fontsize of the figure title

num = 0

def show_data(df):
  global num
  months = df.month_year.sort_values().unique()
  fig, ax = plt.subplots(figsize=(50, 30), dpi=300)
  average_sentiment = df.groupby('month_year').mean()
  average_sentiment['averaged_sentiment'] = (average_sentiment.huggingface_sentiment + average_sentiment.spacy_sentiment) / 2

  ax.plot(months, average_sentiment.huggingface_sentiment, linewidth = 10)
  ax.plot(months, average_sentiment.spacy_sentiment, linewidth = 10)
  ax.plot(months, average_sentiment.averaged_sentiment, linewidth = 10)
  plt.legend(['distilRoBERTa Sentiment', 'SpaCy Sentiment', 'Averaged Sentiment'], prop={'size': 40})
  plt.title('Average Monthly Sentiment', fontsize=40)
  plt.xlabel('Time')
  plt.ylabel('Sentiment')
  plt.xticks(rotation=90)
  # plt.grid()
  plt.grid(b=True, which='major', linestyle='-')
  plt.grid(b=True, which='major', linestyle='--')
  plt.minorticks_on()
  plt.show()
  num += 1
  return average_sentiment
average_sentiment = show_data(sentiment_raw_partner_headlines_2013_19)
average_sentiment = show_data(sentiment_analyst_ratings_2013_19)

In [ ]:
# average_sentiment.drop(columns=['year'], inplace=True)
average_sentiment.to_csv('drive/MyDrive/Datathon/Data/sentiment-stocks/analyst_ratings_monthly_avg_sentiment.csv')

In [ ]:
average_sentiment['month'] = average_sentiment.index
average_sentiment.to_csv('drive/MyDrive/Datathon/Data/sentiment-stocks/sentiment_analyst_ratings.csv', index=False)

In [ ]:
sentiment_raw_partner_headlines_2013_19['huggingface_sentiment'] = scores_list
sentiment_raw_partner_headlines_2013_19.to_csv(sentiment_raw_partner_headlines_2013_19_fp, index=False)

# let's plot sentiment against time

## Sentiment Analyst Ratings

In [ ]:
if 'Unnamed: 0' in sentiment_analyst_ratings.columns:
  sentiment_analyst_ratings.drop(columns=['Unnamed: 0'], inplace=True)
sentiment_analyst_ratings = sentiment_analyst_ratings.loc[sentiment_analyst_ratings.stock.notna()]

In [ ]:
sentiment_analyst_ratings.info()

In [ ]:
sentiment_analyst_ratings['month_year'] = sentiment_analyst_ratings.date.apply(lambda x: x[:7])

In [ ]:
mean_sentiment_analyst = sentiment_analyst_ratings.groupby('month_year').mean()
mean_sentiment_analyst

In [ ]:
import seaborn as sns
sns.set(rc={'figure.figsize': (50, 30)})

plt.plot(mean_sentiment_analyst.index, mean_sentiment_analyst.spacy_sentiment)
plt.title('Average Monthly Sentiment')
plt.xlabel = 'month'
plt.xticks(rotation=90)
plt.show()

In [ ]:
mean_sentiment_analyst.spacy_sentiment.min(), mean_sentiment_analyst.spacy_sentiment.max()

In [ ]:
mean_sentiment_analyst['month'] = mean_sentiment_analyst.index
mean_sentiment_analyst.to_csv("/content/drive/MyDrive/Datathon/Data/sentiment-stocks/analyst_ratings_average_monthly_sentiment.csv", index=False)

## Headlines

In [ ]:
sentiment_raw_partner_headlines.info()

In [ ]:
lc = sentiment_raw_partner_headlines.loc[lc]
lc.append(sentiment_raw_partner_headlines.loc[l_c])

In [ ]:
avg_monthly_sentiment = lc.groupby('month_year').mean()
plt.plot(avg_monthly_sentiment.index, avg_monthly_sentiment.spacy_sentiment)
plt.title('Average Monthly Sentiment')
plt.xlabel = 'month'
plt.xticks(rotation=90)
plt.show()

In [ ]:
def drop_if_present(data, columns=[]):
  for col in columns:
    if col in data.columns:
      data.drop(columns=[col], inplace=True)
drop_if_present(sentiment_raw_partner_headlines, ['Unnamed: 0', 'url'])

In [ ]:
sentiment_raw_partner_headlines['month_year'] = sentiment_raw_partner_headlines.date.apply(lambda x: x[:7])

In [ ]:
average_monthly_sentiment_headlines = sentiment_raw_partner_headlines.groupby('month_year').mean()

In [ ]:
import seaborn as sns
sns.set(rc={'figure.figsize': (50, 30)})

plt.plot(average_monthly_sentiment_headlines.index, average_monthly_sentiment_headlines.spacy_sentiment)
plt.title('Average Monthly Sentiment')
plt.xlabel = 'month'
plt.xticks(rotation=90)
plt.show()

In [ ]:
average_monthly_sentiment_headlines.month

In [ ]:
average_monthly_sentiment_headlines['month'] = average_monthly_sentiment_headlines.index
average_monthly_sentiment_headlines.to_csv("/content/drive/MyDrive/Datathon/Data/sentiment-stocks/average_monthly_sentiment_headlines.csv", index=False)

# Combine data

In [ ]:
analyst_ratings_sentiment = pd.read_csv('drive/MyDrive/Datathon/Data/sentiment-stocks/analyst_ratings_monthly_avg_sentiment.csv')
partner_headlines_sentiment = pd.read_csv('drive/MyDrive/Datathon/Data/sentiment-stocks/partner_headlines_monthly_avg_sentiment.csv')

In [ ]:
all_data = pd.read_csv("/content/drive/MyDrive/Datathon/Data/new_table.tsv", sep='\t')
# all_data

In [ ]:
avg_sentiment = []

month2str = {
    'Jan': '01',
    'Feb': '02',
    'Mar': '03',
    'Apr': '04',
    'May': '05',
    'Jun': '06',
    'Jul': '07',
    'Aug': '08',
    'Sep': '09',
    'Oct': '10',
    'Nov': '11',
    'Dec': '12'
}

str2month = {val: month for month, val in month2str.items()}

months = all_data.issue_d.unique().tolist()
each_month = [month[4:] + '-' + month2str[month[:3]] for month in months]
analyst_avg_sentiment = {str2month[month[-2:]] + '-' + month[:4]: analyst_ratings_sentiment.loc[analyst_ratings_sentiment.month_year == month, 'averaged_sentiment'].tolist()[0] for month in each_month}
headline_avg_sentiment = {str2month[month[-2:]] + '-' + month[:4]: partner_headlines_sentiment.loc[partner_headlines_sentiment.month_year == month, 'averaged_sentiment'].tolist()[0] for month in each_month}
analyst_avg_sentiment, headline_avg_sentiment

In [ ]:
for (month, analyst_sentiment), (_, headline_sentiment) in zip(analyst_avg_sentiment.items(), headline_avg_sentiment.items()):
  # print(analyst_sentiment, headline_sentiment)
  all_data.loc[all_data.issue_d == month, 'analyst_avg_sentiment'] = analyst_sentiment
  all_data.loc[all_data.issue_d == month, 'headline_avg_sentiment'] = headline_sentiment
all_data

In [ ]:
all_data.to_csv('/content/drive/MyDrive/Datathon/Data/new_table_with_sentiment.tsv', index=False, sep='\t')

# DTI PLOT

In [ ]:
import pandas as pd
accepted = pd.read_csv('/content/drive/MyDrive/Datathon/LC/Lending_Club_Accepted_2014_2018.csv')

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2882: DtypeWarning: Columns (19,59,118,129,130,131,134,135,136,139,145,146,147) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [ ]:
accepted.issue_d.unique()

array(['Dec-2015', 'Nov-2015', 'Oct-2015', 'Sep-2015', 'Aug-2015',
       'Jul-2015', 'Jun-2015', 'May-2015', 'Apr-2015', 'Mar-2015',
       'Feb-2015', 'Jan-2015', 'Mar-2018', 'Feb-2018', 'Jan-2018',
       'Sep-2017', 'Aug-2017', 'Jul-2017', 'Jun-2016', 'May-2016',
       'Apr-2016', 'Sep-2018', 'Aug-2018', 'Jul-2018', 'Jun-2017',
       'May-2017', 'Apr-2017', 'Mar-2016', 'Feb-2016', 'Jan-2016',
       'Dec-2014', 'Nov-2014', 'Oct-2014', 'Sep-2014', 'Aug-2014',
       'Jul-2014', 'Jun-2014', 'May-2014', 'Apr-2014', 'Mar-2014',
       'Feb-2014', 'Jan-2014', 'Dec-2018', 'Nov-2018', 'Oct-2018',
       'Jun-2018', 'May-2018', 'Apr-2018', 'Mar-2017', 'Feb-2017',
       'Jan-2017', 'Sep-2016', 'Aug-2016', 'Jul-2016', 'Dec-2017',
       'Nov-2017', 'Oct-2017', 'Dec-2016', 'Nov-2016', 'Oct-2016'],
      dtype=object)

In [ ]:
mean_accepted =  accepted.groupby('issue_d').mean()

from operator import itemgetter
sns.set_style('white')

SMALL_SIZE = 10
MEDIUM_SIZE = 30
BIGGER_SIZE = 40

plt.rc('font', size=SMALL_SIZE)          # controls default text sizes
plt.rc('axes', titlesize=SMALL_SIZE)     # fontsize of the axes title
plt.rc('axes', labelsize=MEDIUM_SIZE)    # fontsize of the x and y labels
plt.rc('xtick', labelsize=MEDIUM_SIZE)    # fontsize of the tick labels
plt.rc('ytick', labelsize=MEDIUM_SIZE)    # fontsize of the tick labels
plt.rc('legend', fontsize=SMALL_SIZE)    # legend fontsize
plt.rc('figure', titlesize=BIGGER_SIZE)  # fontsize of the figure title

def sort_dates(datestr_series):
    months = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']
    month2index = {month: idx for idx, month in enumerate(months)}
    dates_list = datestr_series.tolist()
    dates_list = [(datestr, month2index[datestr.split('-')[0]], int(datestr.split('-')[1])) for datestr in dates_list]
    return [x[0] for x in sorted(dates_list, key=itemgetter(2, 1))]

def plot_by_time(data):
    months = sort_dates(accepted.issue_d.unique())
    fig, ax = plt.subplots(figsize=(50, 30), dpi=300)
    ax.plot(months, data, linewidth=10)
    plt.ylabel('Dti')
    plt.title("Average Monthly DtI", fontsize=40)
    plt.xlabel('Time')
    plt.xticks(rotation=90)
    plt.grid(b=True, which='major', linestyle='-')
    plt.grid(b=True, which='major', linestyle='--')
    plt.minorticks_on()
    plt.show()
plot_by_time(mean_accepted.dti)